In [2]:
import pandas as pd
import numpy as np
import os
import pickle


In [3]:
delim = ';'

user_count = 100

base_path = '/opt/iui-datarelease1-sose2021/'

Xpickle_file = './X.pickle'

ypickle_file = './y.pickle'

In [4]:
def load_pickles():
    _p = open(Xpickle_file, 'rb')
    X = pickle.load(_p)
    _p.close()
        
    _p = open(ypickle_file, 'rb')
    y = pickle.load(_p)
    _p.close()
    
    return (np.asarray(X, dtype=pd.DataFrame), np.asarray(y, dtype=str))

In [5]:
def load_data():
    if os.path.isfile(Xpickle_file) and os.path.isfile(ypickle_file):
        return load_pickles()
    data = []
    label = []
    for user in range(0, user_count):
        user_path = base_path + str(user) + '/split_letters_csv/'
        for file in os.listdir(user_path):
            file_name = user_path + file
            letter = ''.join(filter(lambda x: x.isalpha(), file))[0]
            data.append(pd.read_csv(file_name, delim))
            label.append(letter)
    return (np.asarray(data, dtype=pd.DataFrame), np.asarray(label, dtype=str))

In [6]:
X, y = load_data()

In [7]:
def save_pickle():
#     _p = open(np.asarray(data, dtype=pd.DataFrame), 'wb')
    _p = open(Xpickle_file, 'wb')
    pickle.dump(X, _p)
    _p.close()

#     _p = open(np.asarray(label, dtype=str), 'wb')
    _p = open(ypickle_file, 'wb')
    pickle.dump(y, _p)
    _p.close()

In [8]:
len(X), len(y)

(13102, 13102)

In [51]:
def plot_data(data):
    fig, axs = plt.subplots(4, 3, figsize=(3*3, 3*4))
    t = data['Millis']
    axs[0][0].plot(t, data['Acc1 X'])
    axs[0][1].plot(t, data['Acc1 Y'])
    axs[0][2].plot(t, data['Acc1 Z'])
    axs[1][0].plot(t, data['Acc2 X'])
    axs[1][1].plot(t, data['Acc2 Y'])
    axs[1][2].plot(t, data['Acc2 Z'])
    axs[2][0].plot(t, data['Gyro X'])
    axs[2][1].plot(t, data['Gyro Y'])
    axs[2][2].plot(t, data['Gyro Z'])
    axs[3][0].plot(t, data['Mag X'])
    axs[3][1].plot(t, data['Mag Y'])
    axs[3][2].plot(t, data['Mag Z'])

    for a in axs:
        for b in a:
            b.plot(t, data['Force'])


In [11]:
# FIRST CELL: set these variables to limit GPU usage.
import os
os.environ['TF_FORCE_GPU_ALLOW_GROWTH'] = 'true'  # this is required
os.environ['CUDA_VISIBLE_DEVICES'] = '2'          # set to '0' for GPU0, '1' for GPU1 or '2' for GPU2. Check "gpustat" in a terminal.

In [57]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder

le = LabelEncoder()
yyt_filtered = le.fit_transform(yy_filtered) # Lables in Zahlenwerte transformiert
XX_filtered = np.asarray(XX_filtered).astype('float64')
XXX_filtered = np.delete(np.delete(XX_filtered, 0, 2), 13,2) # Drops time col and Millis col

In [59]:
X_train, X_test, y_train, y_test = train_test_split(XXX_filtered, yyt_filtered, test_size=0.2, random_state=177013)

print(X_train.shape)
print(X_test.shape)
print(y_train.shape)
print(y_test.shape)

(10271, 456, 13)
(2568, 456, 13)
(10271,)
(2568,)


In [77]:
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout, Activation, Flatten, Conv1D, MaxPooling1D

model = Sequential()

# model.add(Conv1D(32, 3, input_shape = X_train.shape[1:]))
# model.add(Activation('relu'))
# model.add(MaxPooling1D(pool_size=3))

# model.add(Conv1D(32, 3))
# model.add(Activation('relu'))
# model.add(MaxPooling1D(pool_size=3))

model.add(Flatten(input_shape = (456,13)))
model.add(Dense(456, activation = 'relu'))

model.add(Dense(104))

model.add(Dense(26))
model.add(Activation('sigmoid'))

model.compile(
    optimizer = tf.keras.optimizers.Adam(0.001),
    loss = tf.keras.losses.SparseCategoricalCrossentropy(from_logits = True),
    metrics = [tf.keras.metrics.SparseCategoricalAccuracy()],
)

In [78]:
le.inverse_transform(y_test)

array(['K', 'T', 'U', ..., 'F', 'H', 'G'], dtype='<U1')

In [79]:
X_train.shape, y_train.shape

((10271, 456, 13), (10271,))

In [80]:
model.fit(X_train, y_train, 
          epochs=10,
          batch_size=32,
          verbose=1
         )

Epoch 1/10
321/321 [==============================] - 1s 2ms/step - loss: 3635.9205 - sparse_categorical_accuracy: 0.0375
Epoch 2/10
321/321 [==============================] - 1s 2ms/step - loss: 13.2679 - sparse_categorical_accuracy: 0.0344
Epoch 3/10
321/321 [==============================] - 1s 2ms/step - loss: 5.5680 - sparse_categorical_accuracy: 0.0360
Epoch 4/10
321/321 [==============================] - 1s 2ms/step - loss: 58.0553 - sparse_categorical_accuracy: 0.0411
Epoch 5/10
321/321 [==============================] - 1s 2ms/step - loss: 4.0946 - sparse_categorical_accuracy: 0.0382
Epoch 6/10
321/321 [==============================] - 1s 2ms/step - loss: 3.2512 - sparse_categorical_accuracy: 0.0421
Epoch 7/10
321/321 [==============================] - 1s 2ms/step - loss: 3.2490 - sparse_categorical_accuracy: 0.0432
Epoch 8/10
321/321 [==============================] - 1s 2ms/step - loss: 3.2503 - sparse_categorical_accuracy: 0.0411
Epoch 9/10
321/321 [=======================

In [81]:
# Evaluate the model on the test data using `evaluate`
print("Evaluate on test data")
results = model.evaluate(X_test, y_test, batch_size=32)
print("test loss, test acc:", results)

# Generate predictions (probabilities -- the output of the last layer)
# on new data using `predict`
print("Generate predictions for 3 samples")
predictions = model.predict(X_test[:3])
print("predictions shape:", predictions.shape)
fff= [np.argmax(i) for i in predictions]

le.inverse_transform(y_test[:3]), le.inverse_transform(fff)

Evaluate on test data
81/81 [==============================] - 0s 1ms/step - loss: 11.4346 - sparse_categorical_accuracy: 0.0312
test loss, test acc: [11.434555053710938, 0.031152648851275444]
Generate predictions for 3 samples
predictions shape: (3, 26)


(array(['K', 'T', 'U'], dtype='<U1'), array(['R', 'R', 'R'], dtype='<U1'))

In [82]:
exit()